# Intro to Sentinel-1

```{admonition} Learning Objectives
*A 30 minute guide to Sentinel-1 data for SnowEX*
- understand key characteristics of Sentinel-1 InSAR and data products
- find, visualize, interpret Sentinel-1 data products
```

![s1-artist-view](https://earth.esa.int/documents/163813/1151359/Sentinel1_Auto2C.jpeg)


```{seealso}
this tutorial is a quick practical guide and *will not cover InSAR processing*, check out [UNAVCO InSAR Short Courses](https://www.unavco.org/education/professional-development/short-courses/short-courses.html) if you're interested in learning custom processing of SAR data.
```

## Dive right in

Perhaps the easiest way to get started with Sentinel-1 SAR over a SnowEx field cite is to use the radiometric terrain corrected backscatter amplitude data on AWS: https://registry.opendata.aws/sentinel-1-rtc-indigo/ 

So before diving into theory and caveats, let's visualize some data! If you're interested in more advanced workflows with this data see https://github.com/scottyhq/sentinel1-rtc.

In [1]:
# Import libraries
import rioxarray
import hvplot.xarray
import os

# necessary GDAL environment variables
os.environ['GDAL_DISABLE_READDIR_ON_OPEN']='EMPTY_DIR' 
os.environ['AWS_NO_SIGN_REQUEST']='YES' 

In [2]:
url = 's3://sentinel-s1-rtc-indigo/tiles/RTC/1/IW/12/S/YJ/2016/S1B_20161121_12SYJ_ASC/Gamma0_VV.tif'
da = rioxarray.open_rasterio(url, overview_level=3).squeeze('band')
da.hvplot.image(clim=(0,0.4), cmap='gray', 
                aspect='equal', frame_width=400,
                title='S1B_20161121_12SYJ_ASC',
                rasterize=True # important keyword for large rasters!
               )

:DynamicMap   []
   :Image   [x,y]   (value)

## Quick facts

Sentinel-1 is a constellation of two synthetic aperture radar (SAR) satellites operated by the European Space Agency (ESA). Sentinel-1 is the first SAR system with a global monitoring strategy and fully open data policy! S1A launched 3 April 2014, and S1B launched 25 April 2016. There are many observation modes for SAR, over land the most common mode is 'Interferometric Wideswath' (IW), which has the following characteristics:

| wavelength (cm) | resolution (rng x azi m) | swath width (km) | incidence (deg) |
| - | - | - |  - |
| C-band 5.547 | 3x22 | 250 | 33-43 |

Unlike most optical satellite observations, SAR antennas are pointed to the side, resulting in an "line-of-sight" (LOS) incidence angle with respect to the ellipsoid normal vector. A consequence of this viewing geometry is that radar images can have significant distortions known as shadow (for example due to tall mountains) and layover (where large regions perpendicular to incident energy all map to the same pixel).

The [global observation plan](https://sentinels.copernicus.eu/web/sentinel/missions/sentinel-1/observation-scenario) for Sentinel-1 has changed over time, but generally over Europe, you have repeat acquisitions every 6 days, and elsewhere every 12 or 24 days.

Satellite radar intruments record the *amplitude* and *phase* of microwaves that bounce off Earth's surface. These values can be stored as a single complex number, so you'll often encounter SAR images that store complex-valued arrays. {term}`InSAR`, or 'Interferometric Synthetic Aperture Radar', is a common processing pipline to generate phase-change maps or 'interferograms' (which can be related to tectonic surface displacements or snow properties) using two different SAR acquisitions.

```{seealso}
- [ESA Documentation](https://sentinel.esa.int/web/sentinel/missions/sentinel-1)
- [ASF Documentation](https://asf.alaska.edu/data-sets/sar-data-sets/sentinel-1/)
```

## Search and Discovery

### Level-1 Archives
The most common data products you'll encounter for Sentinel-1 are {term}`GRD` (just amplitude) and {term}`SLC` (amplitude+phase). These are [level-1](https://earthdata.nasa.gov/collaborate/open-data-services-and-software/data-information-policy/data-levels) that most scientific products are derived from. Level-1 data is typically stored in *radar* coordinates. At best you'll have ground control points (GCPs) stored in file metadata for approximate geocoding, but you need to use advanced processing pipelines to accurately geocode and generate higher level products {cite:p}`YagueMartinez2016`.

There are many places to access Sentinel-1 SAR data these days. The official repository is [ESA's Copernicus Open Access Hub](https://scihub.copernicus.eu). The Alaska Satellite Facility (ASF) Maintains a mirror of the entire archive, which you can search in a number of ways including [ASF Vertex](https://search.asf.alaska.edu) or [NASA Earthdata Search](https://search.earthdata.nasa.gov/search?fi=SENTINEL-1A%20C-Band%20SAR!SENTINEL-1B%20C-Band%20SAR&as[instrument][0]=SENTINEL-1A%20C-Band%20SAR&as[instrument][1]=SENTINEL-1B%20C-Band%20SAR)). 

### Higher-level products
There are also a growing number of cloud-hosted archives of processed Sentinel-1 data including global $\sigma_0$ radiometric terrain corrected (RTC) in [Google Earth Engine](https://developers.google.com/earth-engine/guides/sentinel1), $\gamma_0$ RTC data as an [AWS public dataset](https://registry.opendata.aws/sentinel-1-rtc-indigo/). Generating higher-level products often requires using a digital elevation model, so it's important to be aware of the *resolution* and *time acquired* of that digitial elevation model. For example, two common free global digital elevation models for processing include:

| Product| Acquisition Date | Coverage | Resolution (m) | Open Access |
| - | - | - |  - | - | 
| [SRTM](https://lpdaac.usgs.gov/products/srtmgl1v003/) | 2000-02-11 | 60$^\circ$N to 60$^\circ$S  | 30  | [link](https://lpdaac.usgs.gov/products/srtmgl1v003/) |
| [Copernicus DEM](https://spacedata.copernicus.eu/web/cscda/dataset-details?articleId=394198) | 2019-12-01 -> | global | 30 | [link](https://registry.opendata.aws/copernicus-dem/) | 


### On-demand products
Some SAR processing algorithms are complicated to configure and resource intensive, so when possible it is nice to take advantages of services to generate higher level products. For example ASF has the HyP3 service which can generate RTC and Interferometric products https://hyp3-docs.asf.alaska.edu

## Amplitude

SAR Backscatter variations can be related to of melting snow {cite:p}`Small2011`. Cross-polarized Sentinel-1 backscatter variation has even been shown to relate to {term}`SWE` {cite:p}`Lievens2019`. Let's use the public RTC data from earlier and interpret values over grand mesa.

In [3]:
# Load a time series we created a VRT with GDAL to faciliate this step
vrtName = 'stack12SYJ.vrt'
da3 = rioxarray.open_rasterio(vrtName, overview_level=3) # 3rd overview level
da3

<xarray.DataArray (band: 201, y: 344, x: 344)>
[23785536 values with dtype=float32]
Coordinates:
  * band         (band) int64 1 2 3 4 5 6 7 8 ... 195 196 197 198 199 200 201
  * y            (y) float64 4.4e+06 4.4e+06 4.399e+06 ... 4.291e+06 4.29e+06
  * x            (x) float64 7.001e+05 7.004e+05 ... 8.093e+05 8.096e+05
    spatial_ref  int64 0
Attributes:
    _FillValue:    0.0
    scale_factor:  1.0
    add_offset:    0.0
    grid_mapping:  spatial_ref

In [4]:
# Need to add time coordinates to this data
import rasterio
import pandas as pd

with rasterio.open(vrtName) as src:
    filenames = src.descriptions
    datetimes = [pd.to_datetime(x[4:12]) for x in filenames]
    
# add new coordinate to existing dimension 
da = da3.assign_coords(time=('band', datetimes))
# make 'time' active coordinate instead of integer band
da = da.swap_dims({'band':'time'})
# Name the dataset (helpful for hvplot calls later on)
da.name = 'Gamma0VV'
da

<xarray.DataArray 'Gamma0VV' (time: 201, y: 344, x: 344)>
[23785536 values with dtype=float32]
Coordinates:
    band         (time) int64 1 2 3 4 5 6 7 8 ... 195 196 197 198 199 200 201
  * y            (y) float64 4.4e+06 4.4e+06 4.399e+06 ... 4.291e+06 4.29e+06
  * x            (x) float64 7.001e+05 7.004e+05 ... 8.093e+05 8.096e+05
    spatial_ref  int64 0
  * time         (time) datetime64[ns] 2016-11-21 2017-01-08 ... 2020-10-18
Attributes:
    _FillValue:    0.0
    scale_factor:  1.0
    add_offset:    0.0
    grid_mapping:  spatial_ref

In [8]:
# use a small bounding box over grand mesa (UTM coordinates)
xmin,xmax,ymin,ymax = [739186, 742748, 4.325443e+06, 4.327356e+06]
daT = da.sel(x=slice(xmin, xmax), 
             y=slice(ymax, ymin)) # gotcha, these are reversed...

from bokeh.models import DatetimeTickFormatter
formatter = DatetimeTickFormatter(months='%b %Y')

all_points = daT.where(daT!=0).hvplot.scatter('time', groupby=[], dynspread=True, datashade=True) 
mean_trend = daT.where(daT!=0, drop=True).mean(dim=['x','y']).hvplot.line(title='North Grand Mesa', color='red')
(all_points * mean_trend).opts(xformatter=formatter)

:DynamicMap   []
   :Overlay
      .RGB.I   :RGB   [time,Gamma0VV]   (R,G,B,A)
      .Curve.I :Curve   [time]   (Gamma0VV)

## Phase

InSAR phase delays can be due to a number of factors including tectonic motions, atmospheric water vapor changes, and ionospheric conditions. The theory relating InSAR phase delays due to propagation in dry snow is described in a classic study by {cite:p}`Guneriussen2001`. Isolating these signals is complicated and more studies like SnowEx are necessary to validate satellite-based SWE extractions with in-situ sensors!

In [ ]:
# 

## Explore more

```{seealso}

This tutorial just scratched the surface of SAR! Here are some other resources to explore:

- documentation for open source [ISCE2](https://github.com/isce-framework/isce2-docs) SAR processing software
- [UAF Microwave Remote Sensing Course](https://radar.community.uaf.edu)
- [SERVIR SAR Handbook](https://servirglobal.net/Global/Articles/Article/2674/sar-handbook-comprehensive-methodologies-for-forest-monitoring-and-biomass-estimation)    
```